# Using a BespokeFit-optimized force field

This is the second notebook in this workshop; start with `bespokefit.ipynb`. Make sure you run this notebook with the `openff-env` environment!

## Load the protein and ligand

In [1]:
from openff.toolkit import Molecule, Topology

protein = Molecule.from_polymer_pdb("../pdb/protein.pdb")
ligand = Molecule.from_file("../sdf/lig_CAT-13a.sdf")
top = Topology.from_molecules([protein, ligand])

top.to_file("complex-bespoke.pdb")

Warning (not error because allow_undefined_stereo=True): RDMol has unspecified stereochemistry. Undefined chiral centers are:
 - Atom C (index 11)
 - Atom C (index 22)
 - Atom C (index 42)
 - Atom C (index 58)
 - Atom C (index 73)
 - Atom C (index 90)
 - Atom C (index 106)
 - Atom C (index 118)
 - Atom C (index 132)
 - Atom C (index 151)
 - Atom C (index 182)
 - Atom C (index 204)
 - Atom C (index 222)
 - Atom C (index 246)
 - Atom C (index 267)
 - Atom C (index 288)
 - Atom C (index 304)
 - Atom C (index 319)
 - Atom C (index 336)
 - Atom C (index 338)
 - Atom C (index 350)
 - Atom C (index 373)
 - Atom C (index 392)
 - Atom C (index 406)
 - Atom C (index 412)
 - Atom C (index 429)
 - Atom C (index 431)
 - Atom C (index 443)
 - Atom C (index 462)
 - Atom C (index 476)
 - Atom C (index 478)
 - Atom C (index 495)
 - Atom C (index 514)
 - Atom C (index 530)
 - Atom C (index 542)
 - Atom C (index 544)
 - Atom C (index 563)
 - Atom C (index 574)
 - Atom C (index 585)
 - Atom C (index 599)


## Prepare the force field

<div class="alert alert-block alert-warning">
<b>🚧 This code is not production-ready</b><br />
In this notebook, we use the SMIRNOFF port of the Amber ff14SB force field. This is currently the only mainstream protein force field that works with the OpenFF Toolkit, but it's slow and hasn't been rigorously checked against the original force field. The Open Force Field Initiative recommends waiting for OpenFF 3.0.0 "Rosemary", which will include protein parameters, before using this in production work.
</div>

In [2]:
from openff.toolkit import ForceField

force_field = ForceField(
    "../offxml/openff-2.0.0_bespoke_cat13a.offxml",
    "ff14sb_off_impropers_0.0.3.offxml",
)

## Investigate parameters assigned to the ligand

In [3]:
from pprint import pprint

labels = force_field.label_molecules(ligand.to_topology())

sage = ForceField("openff-2.0.0.offxml")
amber = ForceField("ff14sb_off_impropers_0.0.3.offxml")

params = []
for indices, parameter in labels[0]["ProperTorsions"].items():
    if sage["ProperTorsions"].get_parameter({"smirks": parameter.smirks}):
        source = "SAGE"
    elif amber["ProperTorsions"].get_parameter({"smirks": parameter.smirks}):
        source = "Amber"
    else:
        source = "BespokeFit"
    params.append((source, indices, {**parameter.to_dict()}))
pprint(params[:6], indent=2, width=-1)

[ ( 'SAGE',
    ( 0,
      3,
      1,
      5),
    { 'id': 't72',
      'idivf1': 1.0,
      'k1': <Quantity(0.899658512, 'kilocalorie / mole')>,
      'periodicity1': 1,
      'phase1': <Quantity(0.0, 'degree')>,
      'smirks': '[#6X3:1]=[#7X2,#7X3+1:2]-[#6X4:3]-[#6X3,#6X4:4]'}),
  ( 'SAGE',
    ( 0,
      3,
      1,
      38),
    { 'id': 't64',
      'idivf1': 1.0,
      'idivf2': 1.0,
      'k1': <Quantity(0.182238503, 'kilocalorie / mole')>,
      'k2': <Quantity(0.0297234237, 'kilocalorie / mole')>,
      'periodicity1': 2,
      'periodicity2': 3,
      'phase1': <Quantity(0.0, 'degree')>,
      'phase2': <Quantity(0.0, 'degree')>,
      'smirks': '[*:1]-[#6X4:2]-[#7X3$(*~[#6X3,#6X2]):3]~[*:4]'}),
  ( 'BespokeFit',
    ( 0,
      3,
      10,
      11),
    { 'id': 't171',
      'idivf1': 1.0,
      'idivf2': 1.0,
      'idivf3': 1.0,
      'idivf4': 1.0,
      'k1': <Quantity(-7.1780942e-08, 'kilocalories_per_mole')>,
      'k2': <Quantity(-0.273116587, 'kilocalories_per_mo

## Box and solvate

In [4]:
import openmm
import openmm.unit as openmm_unit
from pdbfixer import PDBFixer

fixer = PDBFixer("complex-bespoke.pdb")
fixer.addSolvent(
    padding=0.5 * openmm_unit.nanometer, ionicStrength=0.5 * openmm_unit.molar
)

with open("complex-bespoke_solvated.pdb", "w") as f:
    openmm.app.PDBFile.writeFile(fixer.topology, fixer.positions, f)

# Topology.from_openmm would also work here
top = Topology.from_pdb("complex-bespoke_solvated.pdb", unique_molecules=[ligand])

## Prepare OpenMM inputs

In [5]:
omm_topology = top.to_openmm()
omm_system = force_field.create_openmm_system(top)

## Set up the OpenMM `Simulation`

In [6]:
import openmm
import openmm.unit as omm_unit

# Construct and configure a Langevin integrator at 300 K with an appropriate friction constant and time-step
integrator = openmm.LangevinIntegrator(
    300 * omm_unit.kelvin,
    1 / omm_unit.picosecond,
    0.002 * omm_unit.picoseconds,
)

# Combine the topology, system, integrator and initial positions into a simulation
simulation = openmm.app.Simulation(
    omm_topology,
    omm_system,
    integrator,
)
simulation.context.setPositions(top.get_positions().to_openmm())

# Add a reporter to record the structure every 100 steps (0.2 ps)
pdb_reporter = openmm.app.PDBReporter("trajectory-bespoke.pdb", 100)
simulation.reporters.append(pdb_reporter)

## Energy minimize

In [7]:
import numpy as np

simulation.minimizeEnergy(
    tolerance=omm_unit.Quantity(value=50.0, unit=omm_unit.kilojoule_per_mole)
)
minimized_state = simulation.context.getState(
    getPositions=True, getEnergy=True, getForces=True
)

print(
    "Minimised to",
    minimized_state.getPotentialEnergy(),
    "with maximum force",
    max(
        np.sqrt(v.x * v.x + v.y * v.y + v.z * v.z) for v in minimized_state.getForces()
    ),
    minimized_state.getForces().unit.get_symbol(),
)

minimized_coords = minimized_state.getPositions()

Minimised to -1034376.0871673692 kJ/mol with maximum force 1525.6847013011125 kJ/(nm mol)


## Simulate

In [8]:
simulation.context.setVelocitiesToTemperature(simulation.integrator.getTemperature())
simulation.runForClockTime(1.0 * omm_unit.minute)
print(
    f"Completed simulation time: {simulation.integrator.getStepSize() * simulation.currentStep}"
)

Completed simulation time: 6.4 ps


## Visualize

In [9]:
from viz import visualize_protein_ligand

In [10]:
visualize_protein_ligand("trajectory-bespoke.pdb", top)

NGLWidget(max_frame=31)